In [0]:
!pip install geopandas
!pip install osmnx
!pip install dotenv
!pip install tqdm 

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
"""
Data Collection Script for Walk Score and POI Density Analysis
Collects data using a grid-based approach for specified cities.
"""

import os
import time
import math
import requests
import pandas as pd
import geopandas as gpd
import osmnx as ox
from shapely.geometry import box, Point
from tqdm import tqdm
from dotenv import load_dotenv
from pathlib import Path

In [0]:
# Load environment variables
load_dotenv()

True

In [0]:
# =============================================================================
# CONFIGURATION
# =============================================================================

WALK_SCORE_API_KEY = os.getenv("WALK_SCORE_API_KEY")
GRID_SIZE_KM = 0.5  # 0.5km x 0.5km grid squares
TARGET_SQUARES = 60  # Target number of grid squares per city (~12,000 calls for 200 cities)

# Walk Score API limits
WALK_SCORE_DAILY_LIMIT = 5000
WALK_SCORE_SAFETY_STOP = 4500  # Stop before hitting limit
WALK_SCORE_RATE_LIMIT_SECONDS = 0.5  # Sleep between requests

# Incremental save settings
SAVE_INTERVAL = 50  # Save every N rows

# POI categories to count
POI_TAGS = {
    "restaurants": {"amenity": "restaurant"},
    "cafes": {"amenity": "cafe"},
    "transit_stops": {"public_transport": "stop_position"},
    "bus_stops": {"highway": "bus_stop"},
    "supermarkets": {"shop": "supermarket"},
}

In [0]:
def calculate_radius(target_squares: int, grid_size_km: float = GRID_SIZE_KM) -> float:
    """
    Calculate the radius needed to achieve approximately target_squares grid squares.

    Math:
    - Each square is grid_size_km x grid_size_km (e.g., 0.5km x 0.5km = 0.25 sq km)
    - Total Area needed = target_squares * (grid_size_km^2)
    - Radius needed = sqrt(Total_Area / pi)

    Args:
        target_squares: Target number of grid squares
        grid_size_km: Size of each grid square in km (default 0.5km)

    Returns:
        Radius in kilometers
    """
    area_per_square = grid_size_km * grid_size_km  # sq km per grid square
    total_area_needed = target_squares * area_per_square  # total sq km
    radius_km = math.sqrt(total_area_needed / math.pi)
    return radius_km

In [0]:
def generate_city_grid(
    city_name: str,
    target_squares: int = TARGET_SQUARES,
    grid_size_km: float = GRID_SIZE_KM
) -> gpd.GeoDataFrame:
    """
    Generate a grid of coordinates centered on a city with a dynamic radius.

    Uses calculate_radius() to determine the coverage area based on target_squares,
    ensuring consistent data collection across cities of different sizes.

    Args:
        city_name: Name of the city (e.g., 'Tel Aviv, Israel')
        target_squares: Target number of grid squares (default 60)
        grid_size_km: Size of each grid square in km (default 0.5km)

    Returns:
        GeoDataFrame with grid squares and their center coordinates
    """
    # Calculate dynamic radius
    radius_km = calculate_radius(target_squares, grid_size_km)
    grid_size_m = grid_size_km * 1000  # Convert to meters for projection
    radius_m = radius_km * 1000  # Convert to meters

    print(f"Generating grid for {city_name}...")
    print(f"  Target squares: {target_squares}")
    print(f"  Grid size: {grid_size_km}km x {grid_size_km}km")
    print(f"  Calculated radius: {radius_km:.2f}km")

    # Get city center coordinates from OpenStreetMap
    try:
        city_gdf = ox.geocode_to_gdf(city_name)
    except Exception as e:
        raise ValueError(f"Could not geocode city '{city_name}': {e}")

    # Get city center point (centroid of the geocoded area)
    city_center = city_gdf.geometry.iloc[0].centroid

    # Project to UTM for accurate meter-based calculations
    utm_crs = city_gdf.estimate_utm_crs()
    city_gdf_projected = city_gdf.to_crs(utm_crs)
    center_projected = city_gdf_projected.geometry.iloc[0].centroid

    # Define the bounding box based on radius from center
    center_x, center_y = center_projected.x, center_projected.y
    minx = center_x - radius_m
    maxx = center_x + radius_m
    miny = center_y - radius_m
    maxy = center_y + radius_m

    # Create a circular boundary for filtering
    circle_boundary = center_projected.buffer(radius_m)

    # Generate grid cells within the circular area
    grid_cells = []
    grid_id = 0

    x = minx
    while x < maxx:
        y = miny
        while y < maxy:
            # Create grid cell
            cell = box(x, y, x + grid_size_m, y + grid_size_m)

            # Only include cells whose centroid is within the circular radius
            cell_center = cell.centroid
            if cell_center.within(circle_boundary):
                grid_cells.append({
                    "grid_id": grid_id,
                    "geometry": cell,
                })
                grid_id += 1
            y += grid_size_m
        x += grid_size_m

    if len(grid_cells) == 0:
        raise ValueError(f"No grid cells generated for {city_name}. Check city name.")

    # Create GeoDataFrame in projected CRS
    grid_gdf = gpd.GeoDataFrame(grid_cells, crs=utm_crs)

    # Calculate centroids in projected CRS, then convert to lat/lon
    grid_gdf["centroid_projected"] = grid_gdf.geometry.centroid

    # Convert back to WGS84 (lat/lon)
    grid_gdf = grid_gdf.to_crs("EPSG:4326")
    centroids_wgs84 = grid_gdf["centroid_projected"].to_crs("EPSG:4326")

    grid_gdf["center_lat"] = centroids_wgs84.y
    grid_gdf["center_lon"] = centroids_wgs84.x
    grid_gdf = grid_gdf.drop(columns=["centroid_projected"])

    print(f"  Generated {len(grid_gdf)} grid squares (target: {target_squares})")
    return grid_gdf

In [0]:
def count_pois_in_grid(
    grid_gdf: gpd.GeoDataFrame,
    city_name: str,
    target_squares: int = TARGET_SQUARES,
    grid_size_km: float = GRID_SIZE_KM
) -> gpd.GeoDataFrame:
    """
    Count POIs within each grid square using OSMnx.

    Fetches POIs within the same radius-based area used for grid generation.

    Args:
        grid_gdf: GeoDataFrame with grid squares
        city_name: Name of the city for POI query
        target_squares: Target number of grid squares (for radius calculation)
        grid_size_km: Size of each grid square in km

    Returns:
        GeoDataFrame with POI counts added
    """
    print(f"Fetching POI data for {city_name}...")

    # Initialize POI count columns
    for poi_name in POI_TAGS.keys():
        grid_gdf[f"poi_{poi_name}"] = 0
    grid_gdf["poi_total"] = 0

    # Calculate the same radius used for grid generation
    radius_km = calculate_radius(target_squares, grid_size_km)

    # Get city center and create search boundary
    try:
        city_gdf = ox.geocode_to_gdf(city_name)
        city_center = city_gdf.geometry.iloc[0].centroid

        # Create a circular buffer around city center for POI search
        # Buffer distance needs to be in degrees (approximate conversion)
        # 1 degree latitude ≈ 111 km
        buffer_degrees = radius_km / 111.0 * 1.2  # Add 20% buffer to ensure coverage
        search_boundary = city_center.buffer(buffer_degrees)
    except Exception as e:
        print(f"  Warning: Could not create search boundary: {e}")
        return grid_gdf

    # Fetch POIs for each category
    all_pois = {}
    for poi_name, tags in tqdm(POI_TAGS.items(), desc="Fetching POI categories"):
        try:
            pois = ox.features_from_polygon(search_boundary, tags=tags)
            # Convert to points (use centroid for polygons)
            if len(pois) > 0:
                pois = pois.to_crs("EPSG:4326")
                pois_projected = pois.to_crs(pois.estimate_utm_crs())
                pois["point_geom"] = pois_projected.geometry.centroid.to_crs("EPSG:4326")
                all_pois[poi_name] = pois
                print(f"  Found {len(pois)} {poi_name}")
        except Exception as e:
            print(f"  Warning: Could not fetch {poi_name}: {e}")
            all_pois[poi_name] = gpd.GeoDataFrame()

    # Count POIs in each grid square
    print("Counting POIs per grid square...")
    for idx, row in tqdm(grid_gdf.iterrows(), total=len(grid_gdf), desc="Processing grid"):
        grid_cell = row.geometry
        total_count = 0

        for poi_name, pois_gdf in all_pois.items():
            if len(pois_gdf) > 0:
                # Count POIs within this grid cell
                points_in_cell = pois_gdf[pois_gdf["point_geom"].within(grid_cell)]
                count = len(points_in_cell)
                grid_gdf.at[idx, f"poi_{poi_name}"] = count
                total_count += count

        grid_gdf.at[idx, "poi_total"] = total_count

    return grid_gdf

In [0]:
class WalkScoreCollector:
    """
    Collects Walk Score data with rate limiting and safety stops.
    """

    def __init__(self, api_key: str, output_path: Path):
        self.api_key = api_key
        self.output_path = output_path
        self.request_count = 0
        self.base_url = "https://api.walkscore.com/score"

        # Load existing progress if resuming
        self.existing_data = self._load_existing_progress()

    def _load_existing_progress(self) -> set:
        """Load grid IDs that have already been processed."""
        if self.output_path.exists():
            existing_df = pd.read_csv(self.output_path)
            processed_ids = set(existing_df["grid_id"].tolist())
            print(f"Resuming: Found {len(processed_ids)} already processed grid squares")
            return processed_ids
        return set()

    def fetch_walk_score(self, lat: float, lon: float, address: str = ""):
        """
        Fetch Walk Score for a single coordinate.

        Args:
            lat: Latitude
            lon: Longitude
            address: Optional address string

        Returns:
            Walk score value (0-100) or None if unavailable/failed
        """
        params = {
            "format": "json",
            "lat": lat,
            "lon": lon,
            "wsapikey": self.api_key,
        }
        if address:
            params["address"] = address

        try:
            response = requests.get(self.base_url, params=params, timeout=10)
            response.raise_for_status()
            data = response.json()

            # Return walk_score, or None if missing/unavailable
            return data.get("walkscore")
        except requests.RequestException as e:
            print(f"  API error at ({lat}, {lon}): {e}")
            return None

    def collect_for_grid(self, grid_gdf: gpd.GeoDataFrame) -> gpd.GeoDataFrame:
        """
        Collect Walk Scores for all grid squares with safety features.

        Features:
        - Rate limiting (sleep between requests)
        - Auto-stop at safety limit (4500 requests)
        - Incremental saving every 50 rows
        - Resume capability (skips already processed squares)
        """
        if not self.api_key:
            print("ERROR: WALK_SCORE_API_KEY not found in .env file!")
            print("Skipping Walk Score collection.")
            grid_gdf["walk_score"] = None
            return grid_gdf

        # Initialize walk_score column if not present
        if "walk_score" not in grid_gdf.columns:
            grid_gdf["walk_score"] = None

        # Filter to unprocessed grid squares
        unprocessed_mask = ~grid_gdf["grid_id"].isin(self.existing_data)
        unprocessed_indices = grid_gdf[unprocessed_mask].index.tolist()

        print(f"\nWalk Score Collection:")
        print(f"  Total grid squares: {len(grid_gdf)}")
        print(f"  Already processed: {len(self.existing_data)}")
        print(f"  Remaining: {len(unprocessed_indices)}")
        print(f"  Safety limit: {WALK_SCORE_SAFETY_STOP} requests")
        print(f"  Rate limit: {WALK_SCORE_RATE_LIMIT_SECONDS}s between requests\n")

        rows_since_save = 0

        for idx in tqdm(unprocessed_indices, desc="Fetching Walk Scores"):
            # Check safety limit
            if self.request_count >= WALK_SCORE_SAFETY_STOP:
                print(f"\n⚠️  SAFETY STOP: Reached {self.request_count} requests.")
                print(f"    Stopping to preserve API quota.")
                print(f"    Re-run script tomorrow to continue.")
                self._save_progress(grid_gdf)
                break

            row = grid_gdf.loc[idx]
            lat, lon = row["center_lat"], row["center_lon"]

            # Rate limiting
            time.sleep(WALK_SCORE_RATE_LIMIT_SECONDS)

            # Fetch walk score (returns value or None)
            walk_score = self.fetch_walk_score(lat, lon)
            self.request_count += 1

            # Update dataframe (None values become NaN in CSV)
            grid_gdf.at[idx, "walk_score"] = walk_score

            rows_since_save += 1

            # Incremental save
            if rows_since_save >= SAVE_INTERVAL:
                self._save_progress(grid_gdf)
                rows_since_save = 0
                tqdm.write(f"  💾 Saved progress ({self.request_count} API calls made)")

        # Final save
        self._save_progress(grid_gdf)
        print(f"\n✅ Walk Score collection complete. Total API calls: {self.request_count}")

        return grid_gdf

    def _save_progress(self, grid_gdf: gpd.GeoDataFrame):
        """Save current progress to CSV."""
        # Save only rows that have been processed
        processed_mask = grid_gdf["walk_score"].notna() | grid_gdf["grid_id"].isin(self.existing_data)

        # Convert to regular DataFrame for CSV (drop geometry)
        df_to_save = grid_gdf.copy()
        df_to_save["geometry_wkt"] = df_to_save.geometry.to_wkt()
        df_to_save = pd.DataFrame(df_to_save.drop(columns=["geometry"]))

        df_to_save.to_csv(self.output_path, index=False)



In [0]:
def collect_city_data(
    city_name: str,
    output_dir: str = "data",
    collect_pois: bool = True,
    collect_walk_scores: bool = True,
    target_squares: int = TARGET_SQUARES,
    grid_size_km: float = GRID_SIZE_KM,
    mode: str = "grid"
) -> gpd.GeoDataFrame:
    """
    Main function to collect all data for a city.

    Uses dynamic radius calculation to ensure consistent grid square count
    across cities of different sizes.

    Args:
        city_name: Name of the city (e.g., 'Tel Aviv, Israel')
        output_dir: Directory to save output files
        collect_pois: Whether to collect POI data
        collect_walk_scores: Whether to collect Walk Score data
        target_squares: Target number of grid squares per city (default 60)
        grid_size_km: Size of each grid square in km (default 0.5)

    Returns:
        GeoDataFrame with all collected data
    """
    # Create output directory
    output_path = Path(output_dir)
    output_path.mkdir(exist_ok=True)


    # Create safe filename from city name
    safe_city_name = city_name.lower().replace(" ", "_").replace(",", "")

    # File paths
    grid_file = output_path / f"{safe_city_name}_grid.csv"
    poi_file = output_path / f"{safe_city_name}_with_pois.csv"
    final_file = output_path / f"{safe_city_name}_complete.csv"

    # Calculate radius for display
    radius_km = calculate_radius(target_squares, grid_size_km)

    print("=" * 60)
    print(f"DATA COLLECTION: {city_name}")
    print(f"Budget: {target_squares} squares | Radius: {radius_km:.2f}km")
    print("=" * 60)

    # Step 1: Generate grid with dynamic radius
    print("\n[1/3] GRID GENERATION (Dynamic Radius)")
    print("-" * 40)
    #grid_gdf = generate_city_grid(city_name, target_squares, grid_size_km)
    if mode == "center":
        # Generate single square
        grid_gdf = generate_center_square(city_name, grid_size_km)
        # Force radius to be large enough for one square (approx 2 squares area needed for coverage)
        poi_search_squares = 2 
    else:
        # Standard grid generation
        grid_gdf = generate_city_grid(city_name, target_squares, grid_size_km)
        poi_search_squares = target_squares

    # Save grid
    grid_df = grid_gdf.copy()
    grid_df["geometry_wkt"] = grid_df.geometry.to_wkt()
    pd.DataFrame(grid_df.drop(columns=["geometry"])).to_csv(grid_file, index=False)
    print(f"Saved grid to: {grid_file}")

    # Step 2: Collect POI data (free)
    if collect_pois:
        print("\n[2/3] POI DATA COLLECTION (Free)")
        print("-" * 40)
        grid_gdf = count_pois_in_grid(grid_gdf, city_name, target_squares, grid_size_km)

        # Save POI data
        poi_df = grid_gdf.copy()
        poi_df["geometry_wkt"] = poi_df.geometry.to_wkt()
        pd.DataFrame(poi_df.drop(columns=["geometry"])).to_csv(poi_file, index=False)
        print(f"Saved POI data to: {poi_file}")

    # Step 3: Collect Walk Score data (rate limited)
    if collect_walk_scores:
        print("\n[3/3] WALK SCORE COLLECTION (Rate Limited)")
        print("-" * 40)
        collector = WalkScoreCollector(WALK_SCORE_API_KEY, final_file)
        grid_gdf = collector.collect_for_grid(grid_gdf)

    if "," in city_name:
        clean_city, clean_country = [x.strip() for x in city_name.split(",", 1)]
    else:
        clean_city = city_name
        clean_country = "Unknown"

    grid_gdf["city_name"] = clean_city
    grid_gdf["country_name"] = clean_country
    grid_gdf["unique_grid_id"] = grid_gdf.apply(
        lambda row: f"{clean_city}_{clean_country}_{row['grid_id']}".replace(" ", "_"), axis=1
    )

    # Final save
    final_df = grid_gdf.copy()
    final_df["geometry_wkt"] = final_df.geometry.to_wkt()
    pd.DataFrame(final_df.drop(columns=["geometry"])).to_csv(final_file, index=False)

    print("\n" + "=" * 60)
    print("COLLECTION COMPLETE")
    print("=" * 60)
    print(f"Output file: {final_file}")
    print(f"Total grid squares: {len(grid_gdf)}")

    return grid_gdf

In [0]:
# List of cities to collect data for
# Format: "City, Country" (as recognized by OpenStreetMap geocoding)
CITIES = [
    "Kissimmee, United States",
    "Paris, France",
    "London, United Kingdom",
    "Rome, Italy",
    "Dubai, United Arab Emirates",
    "San Francisco, United States",
    "São Paulo, Brazil",
    "Puglia, Italy",
    "Rio de Janeiro, Brazil",
    "Los Angeles, United States",
    "New York, NY, United States",
    "Davenport, United States",
    "Las Vegas, United States",
    "Toronto, Canada",
    "Austin, United States",
    "Athens, Greece",
    "Madrid, Spain",
    "Cape Town, South Africa",
    "Lahaina, United States",
    "Miami, United States",
    "Mexico City, Mexico",
    "San Diego, United States",
    "Kuala Lumpur, Malaysia",
    "Buenos Aires, Argentina",
    "Houston, United States",
    "Florianópolis, Brazil",
    "Orlando, United States",
    "Kihei, United States",
    "Panama City Beach, United States",
    "Seattle, United States",
    "Nashville, United States",
    "Copenhagen, Denmark",
    "Atlanta, United States",
    "Barcelona, Spain",
    "Milan, Italy",
    "Medellín, Colombia",
    "Myrtle Beach, United States",
    "Nice, France",
    "Lisbon, Portugal",
    "Bogotá, Colombia",
    "Destin, United States",
    "Dallas, United States",
    "Málaga, Spain",
    "Riyadh, Saudi Arabia",
    "Budapest, Hungary",
    "Sevierville, United States",
    "Marseille, France",
    "Chicago, United States",
    "Florence, Italy",
    "Washington, United States",
    "South Lake Tahoe, United States",
    "Scottsdale, United States",
    "Porto, Portugal",
    "Honolulu, United States",
    "Phoenix, United States",
    "Seoul, South Korea",
    "Vienna, Austria",
    "New Orleans, United States",
    "Miramar Beach, United States",
    "Playa del Carmen, Mexico",
    "Denver, United States",
    "San Antonio, United States",
    "Marrakesh, Morocco",
    "Cannes, France",
    "Portland, OR, United States",
    "Tampa, United States",
    "Hilton Head Island, United States",
    "Park City, United States",
    "Oakland, United States",
    "Osaka, Japan",
    "Ocean City, United States",
    "Amsterdam, Netherlands",
    "Breckenridge, United States",
    "Gulf Shores, United States",
    "Santa Rosa Beach, United States",
    "Ubatuba, Brazil",
    "Berlin, Germany",
    "Palm Springs, United States",
    "Cape Coral, United States",
    "Tulum, Mexico",
    "Marbella, Spain",
    "Tucson, United States",
    "Truckee, United States",
    "Miami Beach, United States",
    "Philadelphia, United States",
    "Warsaw, Poland",
    "Orange Beach, United States",
    "Fort Lauderdale, United States",
    "Venice, Italy",
    "Kraków, Poland",
    "Naples, FL, United States",
    "Tbilisi, Georgia",
    "Praia Grande, Brazil",
    "North Myrtle Beach, United States",
    "Nairobi, Kenya",
    "Hollywood, FL, United States",
    "St. Augustine, United States",
    "Seville, Spain",
    "Pattaya City, Thailand",
    "Naples, Italy",
    "Steamboat Springs, United States",
    "Gatlinburg, United States",
    "Sarasota, United States",
    "Tel Aviv-Yafo, Israel",
    "Montreal, Canada",
    "San Jose, United States",
    "Valencia, Spain",
    "Cancún, Mexico",
    "Guarujá, Brazil",
    "Charlotte, United States",
    "Puerto Vallarta, Mexico",
    "Split, Croatia",
    "Branson, United States",
    "Edinburgh, United Kingdom",
    "Galveston, United States",
    "Auckland, New Zealand",
    "Big Bear Lake, United States",
    "Indianapolis, United States",
    "Salvador, Brazil",
    "Lyon, France",
    "Batumi, Georgia",
    "Mazatlan, Mexico",
    "Fort Walton Beach, United States",
    "Colorado Springs, United States",
    "Gdańsk, Poland",
    "Santo Domingo, Dominican Republic",
    "Kailua-Kona, United States",
    "Palermo, Italy",
    "Jacksonville, United States",
    "Beyoğlu, Turkey",
    "Four Corners, United States",
    "Columbus, United States",
    "Cornwall, United Kingdom",
    "Quezon City, Philippines",
    "Munich, Germany",
    "Louisville, United States",
    "Savannah, United States",
    "Punta Cana, Dominican Republic",
    "Palm Desert, United States",
    "Cabo Frio, Brazil",
    "Dubrovnik, Croatia",
    "Guadalajara, Mexico",
    "Johor Bahru, Malaysia",
    "Bengaluru, India",
    "Boston, United States",
    "Newark, United States",
    "Jeju-si, South Korea",
    "Belgrade, Serbia",
    "Mammoth Lakes, United States",
    "Sedona, United States",
    "Santiago, Chile",
    "Albufeira, Portugal",
    "Broken Bow, United States",
    "San Juan, Puerto Rico",
    "Pigeon Forge, United States",
    "Cali, Colombia",
    "Torino, Italy",
    "Brasília, Brazil",
    "Antibes, France",
    "Calgary, Canada",
    "Port Aransas, United States",
    "Balneário Camboriú, Brazil",
    "Wilmington, United States",
    "Toulouse, France",
    "Cebu City, Philippines",
    "Cusco, Peru",
    "San Carlos de Bariloche, Argentina",
    "Kyiv, Ukraine",
    "Quito, Ecuador",
    "Bordeaux, France",
    "Annecy, France",
    "Granada, Spain",
    "Havana, Cuba",
    "Naxos, Greece",
    "Pittsburgh, United States",
    "Pensacola, United States",
    "Arlington, United States",
    "Vail, United States",
    "Alicante, Spain",
    "Montpellier, France",
    "Benalmádena, Spain",
    "South Padre Island, United States",
    "Bend, United States",
    "Daytona Beach, United States",
    "Pasay, Philippines",
    "Punta del Este, Uruguay",
    "São Sebastião, Brazil",
    "Albuquerque, United States",
    "Charleston, United States",
    "St. Louis, United States",
    "Acapulco de Juárez, Mexico",
    "Long Beach, United States",
    "João Pessoa, Brazil",
    "Richmond, United States",
    "Mar del Plata, Argentina",
    "Salt Lake City, United States",
    "Tahoe City, United States",
    "Chania, Greece",
]

In [0]:
all_cities_dfs = []
failed_cities = []

print(f"Starting collection for {len(CITIES)} cities...")

for city in CITIES:
    try:
        result = collect_city_data(
            city_name=city,
            output_dir="poi_data",
            collect_pois=True,
            collect_walk_scores=False,
        )
        
        all_cities_dfs.append(result)

        print(f"\nSuccessfully collected data for {city}")
    except Exception as e:
        print(f"\nError collecting data for {city}: {e}")
        failed_cities.append(city)
        continue



Starting collection for 198 cities...
DATA COLLECTION: Kissimmee, United States
Budget: 60 squares | Radius: 2.19km

[1/3] GRID GENERATION (Dynamic Radius)
----------------------------------------
Generating grid for Kissimmee, United States...
  Target squares: 60
  Grid size: 0.5km x 0.5km
  Calculated radius: 2.19km
  Generated 62 grid squares (target: 60)
Saved grid to: poi_data/kissimmee_united_states_grid.csv

[2/3] POI DATA COLLECTION (Free)
----------------------------------------
Fetching POI data for Kissimmee, United States...


Fetching POI categories:  20%|██        | 1/5 [01:07<04:29, 67.48s/it]

  Found 19 restaurants


Fetching POI categories:  40%|████      | 2/5 [04:11<06:47, 135.98s/it]

  Found 3 cafes


...

Fetching POI categories: 100%|██████████| 5/5 [01:12<00:00, 14.55s/it]


  Found 4 supermarkets
Counting POIs per grid square...


Processing grid: 100%|██████████| 62/62 [00:00<00:00, 331.44it/s]


Saved POI data to: poi_data/salt_lake_city_united_states_with_pois.csv

COLLECTION COMPLETE
Output file: poi_data/salt_lake_city_united_states_complete.csv
Total grid squares: 62

Successfully collected data for Salt Lake City, United States
DATA COLLECTION: Tahoe City, United States
Budget: 60 squares | Radius: 2.19km

[1/3] GRID GENERATION (Dynamic Radius)
----------------------------------------
Generating grid for Tahoe City, United States...
  Target squares: 60
  Grid size: 0.5km x 0.5km
  Calculated radius: 2.19km

Error collecting data for Tahoe City, United States: Could not geocode city 'Tahoe City, United States': Nominatim did not geocode query 'Tahoe City, United States' to a geometry of type (Multi)Polygon.
DATA COLLECTION: Chania, Greece
Budget: 60 squares | Radius: 2.19km

[1/3] GRID GENERATION (Dynamic Radius)
----------------------------------------
Generating grid for Chania, Greece...
  Target squares: 60
  Grid size: 0.5km x 0.5km
  Calculated radius: 2.19km

Error

---------------------------------------------------------------------------
OSError                                   Traceback (most recent call last)
File <command-5227413656589827>, line 64
     61     cols = ['unique_grid_id', 'city_name', 'country_name'] + [c for c in combined_df.columns if c not in ['unique_grid_id', 'city_name', 'country_name']]
     62     combined_df = combined_df[cols]
---> 64     combined_df.to_csv(master_output_path, index=False)
     65     print(f"✅ Master dataset updated. Total rows: {len(combined_df)}")
     67 else:

File /databricks/python/lib/python3.12/site-packages/pandas/util/_decorators.py:333, in deprecate_nonkeyword_arguments.<locals>.decorate.<locals>.wrapper(*args, **kwargs)
    327 if len(args) > num_allow_args:
    328     warnings.warn(
    329         msg.format(arguments=_format_argument_list(allow_args)),
    330         FutureWarning,
    331         stacklevel=find_stack_level(),
    332     )
--> 333 return func(*args, **kwargs)

Fil

In [0]:
# Check which cities from the original list don't have files
from pathlib import Path

poi_data_dir = Path("poi_data")
existing_files = {f.stem.replace("_complete", "") for f in poi_data_dir.glob("*_complete.csv")}

failed_cities = []
for city in CITIES:
    safe_name = city.lower().replace(" ", "_").replace(",", "")
    if safe_name not in existing_files:
        failed_cities.append(city)

print(f"Failed cities ({len(failed_cities)}):")
for city in failed_cities:
    print(f"  - {city}")

Failed cities (7):
  - Athens, Greece
  - Cape Town, South Africa
  - Santa Rosa Beach, United States
  - Punta Cana, Dominican Republic
  - Albuquerque, United States
  - Tahoe City, United States
  - Chania, Greece


In [0]:
# Handle cities with errors

RETRY_CITIES = [
    # Cities (likely to work - have polygon boundaries)
    "Municipality of Athens, Greece",
    "Punta Cana, Higüey, La Altagracia, Dominican Republic",
    "Albuquerque, Bernalillo County, New Mexico, United States",
    "Municipality of Chania, Greece",
    
    # Town/Village (might fail - often no polygon)
    "Santa Rosa Beach, Walton County, Florida, United States",
    "Tahoe City, Placer County, California, United States",
]


for city in RETRY_CITIES:
    try:
        result = collect_city_data(
            city_name=city,
            output_dir="poi_data",
            collect_pois=True,
            collect_walk_scores=False,
        )
        print(f"\nSuccessfully collected data for {city}")
    except Exception as e:
        print(f"\nError collecting data for {city}: {e}")
        continue

DATA COLLECTION: Municipality of Athens, Greece
Budget: 60 squares | Radius: 2.19km

[1/3] GRID GENERATION (Dynamic Radius)
----------------------------------------
Generating grid for Municipality of Athens, Greece...
  Target squares: 60
  Grid size: 0.5km x 0.5km
  Calculated radius: 2.19km
  Generated 62 grid squares (target: 60)
Saved grid to: poi_data/municipality_of_athens_greece_grid.csv

[2/3] POI DATA COLLECTION (Free)
----------------------------------------
Fetching POI data for Municipality of Athens, Greece...


Fetching POI categories:  20%|██        | 1/5 [00:07<00:30,  7.52s/it]

  Found 704 restaurants


Fetching POI categories:  40%|████      | 2/5 [00:09<00:13,  4.53s/it]

  Found 851 cafes


...

  Found 36 bus_stops


Fetching POI categories: 100%|██████████| 5/5 [00:06<00:00,  1.39s/it]


  Found 5 supermarkets
Counting POIs per grid square...


Processing grid: 100%|██████████| 62/62 [00:00<00:00, 485.86it/s]


Saved POI data to: poi_data/municipality_of_chania_greece_with_pois.csv

COLLECTION COMPLETE
Output file: poi_data/municipality_of_chania_greece_complete.csv
Total grid squares: 62

Successfully collected data for Municipality of Chania, Greece
DATA COLLECTION: Santa Rosa Beach, Walton County, Florida, United States
Budget: 60 squares | Radius: 2.19km

[1/3] GRID GENERATION (Dynamic Radius)
----------------------------------------
Generating grid for Santa Rosa Beach, Walton County, Florida, United States...
  Target squares: 60
  Grid size: 0.5km x 0.5km
  Calculated radius: 2.19km

Error collecting data for Santa Rosa Beach, Walton County, Florida, United States: Could not geocode city 'Santa Rosa Beach, Walton County, Florida, United States': Nominatim did not geocode query 'Santa Rosa Beach, Walton County, Florida, United States' to a geometry of type (Multi)Polygon.
DATA COLLECTION: Tahoe City, Placer County, California, United States
Budget: 60 squares | Radius: 2.19km

[1/3] GRI

In [0]:
import pandas as pd
import geopandas as gpd
from shapely.geometry import box, Point
import osmnx as ox
from tqdm import tqdm
from pathlib import Path
import math

# Cities that need coordinate-based collection
COORD_FALLBACK = {
    "Punta Cana, Dominican Republic": (18.5601, -68.3725),
    "Albuquerque, United States": (35.0844, -106.6504),
    "Santa Rosa Beach, United States": (30.3930, -86.2286),
    "Tahoe City, United States": (39.1677, -120.1427),
    "Cape Town, South Africa": (-33.9249, 18.4241),
}

def collect_city_data_from_coords(city_name, lat, lon, output_dir="poi_data", target_squares=60, grid_size_km=0.5):
    """Collect POI data using coordinates instead of city name"""
    
    output_path = Path(output_dir)
    output_path.mkdir(exist_ok=True)
    
    # Parse city and country
    parts = [x.strip() for x in city_name.split(",")]
    clean_city = parts[0]
    clean_country = parts[-1] if len(parts) > 1 else "Unknown"
    safe_city_name = city_name.lower().replace(" ", "_").replace(",", "")
    
    print("=" * 60)
    print(f"DATA COLLECTION (coords): {city_name}")
    print(f"Coordinates: ({lat}, {lon})")
    print("=" * 60)
    
    # Generate grid from coordinates
    print("\n[1/2] GRID GENERATION")
    radius_km = math.sqrt(target_squares) * grid_size_km / 2
    
    lat_deg_per_km = 1 / 111.0
    lon_deg_per_km = 1 / (111.0 * math.cos(math.radians(lat)))
    grid_size_lat = grid_size_km * lat_deg_per_km
    grid_size_lon = grid_size_km * lon_deg_per_km
    radius_lat = radius_km * lat_deg_per_km
    radius_lon = radius_km * lon_deg_per_km
    
    minx, maxx = lon - radius_lon, lon + radius_lon
    miny, maxy = lat - radius_lat, lat + radius_lat
    
    grid_cells = []
    grid_id = 0
    current_lat = miny
    while current_lat < maxy:
        current_lon = minx
        while current_lon < maxx:
            cell = box(current_lon, current_lat, current_lon + grid_size_lon, current_lat + grid_size_lat)
            grid_cells.append({
                'grid_id': grid_id,
                'geometry': cell,
                'center_lat': current_lat + grid_size_lat / 2,
                'center_lon': current_lon + grid_size_lon / 2,
            })
            grid_id += 1
            current_lon += grid_size_lon
        current_lat += grid_size_lat
    
    grid_gdf = gpd.GeoDataFrame(grid_cells, crs="EPSG:4326")
    print(f"  Generated {len(grid_gdf)} grid squares")
    
    # Collect POIs
    print("\n[2/2] POI DATA COLLECTION")
    radius_m = radius_km * 1000 * 1.5
    
    poi_categories = {
        "restaurants": {"amenity": "restaurant"},
        "cafes": {"amenity": "cafe"},
        "transit_stops": {"public_transport": "stop_position"},
        "bus_stops": {"highway": "bus_stop"},
        "supermarkets": {"shop": "supermarket"},
    }
    
    for poi_name in poi_categories:
        grid_gdf[f"poi_{poi_name}"] = 0
    grid_gdf["poi_total"] = 0
    
    all_pois = {}
    for poi_name, tags in tqdm(poi_categories.items(), desc="Fetching POIs"):
        try:
            pois = ox.features_from_point((lat, lon), tags=tags, dist=radius_m)
            all_pois[poi_name] = pois
            print(f"  Found {len(pois)} {poi_name}")
        except:
            all_pois[poi_name] = None
    
    # Count POIs per grid
    for idx, row in tqdm(grid_gdf.iterrows(), total=len(grid_gdf), desc="Counting"):
        total = 0
        for poi_name, pois_gdf in all_pois.items():
            if pois_gdf is not None and len(pois_gdf) > 0:
                pois_gdf = pois_gdf.copy()
                pois_gdf["point_geom"] = pois_gdf.geometry.centroid
                count = len(pois_gdf[pois_gdf["point_geom"].within(row.geometry)])
                grid_gdf.at[idx, f"poi_{poi_name}"] = count
                total += count
        grid_gdf.at[idx, "poi_total"] = total
    
    # Add metadata and save
    grid_gdf["city_name"] = clean_city
    grid_gdf["country_name"] = clean_country
    grid_gdf["unique_grid_id"] = grid_gdf.apply(
        lambda r: f"{clean_city}_{clean_country}_{r['grid_id']}".replace(" ", "_"), axis=1)
    
    final_file = output_path / f"{safe_city_name}_complete.csv"
    final_df = grid_gdf.copy()
    final_df["geometry_wkt"] = final_df.geometry.to_wkt()
    pd.DataFrame(final_df.drop(columns=["geometry"])).to_csv(final_file, index=False)
    
    print(f"\n✅ Saved to: {final_file}")
    print(f"Total grid squares: {len(grid_gdf)}")
    return grid_gdf

# Run for all failed cities
for city_name, (lat, lon) in COORD_FALLBACK.items():
    try:
        collect_city_data_from_coords(city_name, lat, lon, output_dir="poi_data")
    except Exception as e:
        print(f"\n❌ {city_name}: {e}")

DATA COLLECTION (coords): Punta Cana, Dominican Republic
Coordinates: (18.5601, -68.3725)

[1/2] GRID GENERATION
  Generated 64 grid squares

[2/2] POI DATA COLLECTION


Fetching POIs:  20%|██        | 1/5 [00:01<00:05,  1.28s/it]

  Found 19 restaurants


Fetching POIs:  40%|████      | 2/5 [00:02<00:03,  1.29s/it]

  Found 3 cafes


...

  Found 212 bus_stops


Fetching POIs: 100%|██████████| 5/5 [00:06<00:00,  1.39s/it]


  Found 24 supermarkets


Counting:   0%|          | 0/64 [00:00<?, ?it/s]/home/spark-412210d7-c3c8-45b9-bf27-70/.ipykernel/3889/command-7365365094603503-147580099:100: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  pois_gdf["point_geom"] = pois_gdf.geometry.centroid
/home/spark-412210d7-c3c8-45b9-bf27-70/.ipykernel/3889/command-7365365094603503-147580099:100: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  pois_gdf["point_geom"] = pois_gdf.geometry.centroid
/home/spark-412210d7-c3c8-45b9-bf27-70/.ipykernel/3889/command-7365365094603503-147580099:100: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  po


✅ Saved to: poi_data/cape_town_south_africa_complete.csv
Total grid squares: 64


In [0]:
# Cell to combine all POI data from poi_data folder into a single file

import pandas as pd
import os
from pathlib import Path

# Path to the folder with collected data
poi_data_dir = Path("poi_data")

# Find all complete CSV files (or with_pois if complete doesn't exist)
all_files = list(poi_data_dir.glob("*_complete.csv"))

# If no complete files, try with_pois files
if not all_files:
    all_files = list(poi_data_dir.glob("*_with_pois.csv"))
    print("No _complete.csv files found, using _with_pois.csv files")

print(f"Found {len(all_files)} city data files to combine")

# Read and combine all files
all_dfs = []
for file_path in all_files:
    try:
        df = pd.read_csv(file_path)
        all_dfs.append(df)
        print(f"✓ Loaded {file_path.name}: {len(df)} rows")
    except Exception as e:
        print(f"✗ Error loading {file_path.name}: {e}")

# Combine all dataframes
if all_dfs:
    combined_df = pd.concat(all_dfs, ignore_index=True)
    
    # Remove duplicates based on unique_grid_id if it exists
    if 'unique_grid_id' in combined_df.columns:
        before_dedupe = len(combined_df)
        combined_df = combined_df.drop_duplicates(subset=['unique_grid_id'], keep='last')
        after_dedupe = len(combined_df)
        if before_dedupe > after_dedupe:
            print(f"\nRemoved {before_dedupe - after_dedupe} duplicate rows")
    
    # Reorder columns to put identifiers first
    id_cols = ['unique_grid_id', 'city_name', 'country_name']
    existing_id_cols = [c for c in id_cols if c in combined_df.columns]
    other_cols = [c for c in combined_df.columns if c not in id_cols]
    combined_df = combined_df[existing_id_cols + other_cols]
    
    # Create output directory and save
    os.makedirs("poi_data", exist_ok=True)
    output_path = "poi_data/GLOBAL_MASTER_DATASET.csv"
    combined_df.to_csv(output_path, index=False)
    
    print("\n" + "=" * 60)
    print("COMBINATION COMPLETE")
    print("=" * 60)
    print(f"Total cities: {combined_df['city_name'].nunique() if 'city_name' in combined_df.columns else 'N/A'}")
    print(f"Total grid squares: {len(combined_df)}")
    print(f"Output saved to: {output_path}")
    print(f"\nColumns: {list(combined_df.columns)}")
else:
    print("\n⚠️ No data files were successfully loaded!")

Found 199 city data files to combine
✓ Loaded paris_france_complete.csv: 62 rows
✓ Loaded toronto_canada_complete.csv: 62 rows
✓ Loaded rio_de_janeiro_brazil_complete.csv: 62 rows
✓ Loaded london_united_kingdom_complete.csv: 62 rows
✓ Loaded madrid_spain_complete.csv: 62 rows
✓ Loaded orlando_united_states_complete.csv: 62 rows
✓ Loaded barcelona_spain_complete.csv: 62 rows
✓ Loaded myrtle_beach_united_states_complete.csv: 62 rows
✓ Loaded vienna_austria_complete.csv: 62 rows
✓ Loaded tampa_united_states_complete.csv: 62 rows
✓ Loaded scottsdale_united_states_complete.csv: 62 rows
✓ Loaded praia_grande_brazil_complete.csv: 62 rows
✓ Loaded truckee_united_states_complete.csv: 62 rows
✓ Loaded tel_aviv-yafo_israel_complete.csv: 62 rows
✓ Loaded cancún_mexico_complete.csv: 62 rows
✓ Loaded quezon_city_philippines_complete.csv: 62 rows
✓ Loaded guadalajara_mexico_complete.csv: 62 rows
✓ Loaded albufeira_portugal_complete.csv: 62 rows
✓ Loaded punta_del_este_uruguay_complete.csv: 62 rows
✓ 

In [0]:
    
# master_output_path = "data_poi/GLOBAL_MASTER_DATASET.csv"

# if all_cities_dfs:
#     print("\n" + "=" * 60)
#     print("UPDATING MASTER DATASET")
#     print("=" * 60)

#     new_data_gdf = pd.concat(all_cities_dfs, ignore_index=True)
#     if 'geometry' in new_data_gdf.columns:
#         new_data_gdf["geometry_wkt"] = new_data_gdf.geometry.to_wkt()
#         new_data_df = pd.DataFrame(new_data_gdf.drop(columns=["geometry"]))
#     else:
#         new_data_df = pd.DataFrame(new_data_gdf)

#     if os.path.exists(master_output_path):
#         print(f"Found existing dataset at {master_output_path}")
#         try:
#             existing_df = pd.read_csv(master_output_path)
#             print(f"  - Existing rows: {len(existing_df)}")
#             print(f"  - New rows to add: {len(new_data_df)}")
            
#             combined_df = pd.concat([existing_df, new_data_df], ignore_index=True)
            
#             before_dedupe = len(combined_df)
#             combined_df = combined_df.drop_duplicates(subset=['unique_grid_id'], keep='last')
#             after_dedupe = len(combined_df)
            
#             if before_dedupe > after_dedupe:
#                 print(f"  - Removed {before_dedupe - after_dedupe} duplicate grid squares")
            
#         except Exception as e:
#             print(f"⚠️ Error reading existing file: {e}. Creating new file instead.")
#             combined_df = new_data_df
#     else:
#         print("No existing dataset found. Creating new one.")
#         combined_df = new_data_df

#     cols = ['unique_grid_id', 'city_name', 'country_name'] + [c for c in combined_df.columns if c not in ['unique_grid_id', 'city_name', 'country_name']]
#     combined_df = combined_df[cols]

#     combined_df.to_csv(master_output_path, index=False)
#     print(f"✅ Master dataset updated. Total rows: {len(combined_df)}")
    
# else:
#     print("\n⚠️ No new data collected in this run. Master dataset untouched.")

# # print failed cities
# if failed_cities:
#     print("\n" + "=" * 60)
#     print("FAILED CITIES")
#     print("=" * 60)

#     for i, city in enumerate(failed_cities):
#         print(f"{i+1}. {city}")

## center only scraping

In [0]:
def generate_center_square(city_name: str, grid_size_km: float = 0.5) -> gpd.GeoDataFrame:
    """Helper function to create a single square centered on the city."""
    print(f"Generating single center square for {city_name}...")
    
    # 1. Geocode and Project
    try:
        city_gdf = ox.geocode_to_gdf(city_name)
    except Exception as e:
        raise ValueError(f"Could not geocode city '{city_name}': {e}")

    utm_crs = city_gdf.estimate_utm_crs()
    city_gdf_projected = city_gdf.to_crs(utm_crs)
    
    # Get the precise center point (in meters)
    center_point = city_gdf_projected.geometry.iloc[0].centroid
    
    # 2. Create Box (Square)
    half_side_m = (grid_size_km * 1000) / 2
    square_geom = box(
        center_point.x - half_side_m, center_point.y - half_side_m,
        center_point.x + half_side_m, center_point.y + half_side_m
    )
    
    # 3. Create GeoDataFrame in UTM
    grid_gdf = gpd.GeoDataFrame([{'grid_id': 0, 'geometry': square_geom}], crs=utm_crs)
    
    # --- תיקון: חישוב המרכז כשאנחנו עדיין במטרים (UTM) ---
    # זה מונע את האזהרה ומדויק יותר
    centroid_series_utm = grid_gdf.geometry.centroid
    
    # 4. Convert Grid to WGS84 (Lat/Lon) for final output
    grid_gdf = grid_gdf.to_crs("EPSG:4326")
    
    # 5. Convert Centroids to WGS84 separately to get the columns
    centroid_series_wgs84 = centroid_series_utm.to_crs("EPSG:4326")
    
    grid_gdf["center_lat"] = centroid_series_wgs84.y
    grid_gdf["center_lon"] = centroid_series_wgs84.x
    
    return grid_gdf

In [0]:
TIER2_CITIES = [
    "Clearwater, United States",
    "Raleigh, United States",
    "Fredericksburg, United States",
    "Anchorage, United States",
    "Thessaloniki, Greece",
    "Bombinhas, Brazil",
    "Jersey City, United States",
    "Lima, Peru",
    "Cleveland, United States",
    "Wrocław, Poland",
    "Bucharest, Romania",
    "Milano, Italy",
    "Vancouver, Canada",
    "Busan, South Korea",
    "Williamsburg, United States",
    "Santa Marta, Colombia",
    "Minneapolis, United States",
    "Bologna, Italy",
    "Zadar, Croatia",
    "Porto Seguro, Brazil",
    "West Midlands, United Kingdom",
    "Accra, Ghana",
    "Tiranë, Albania",
    "Casablanca, Morocco",
    "Kaş, Turkey",
    "Armação dos Búzios, Brazil",
    "Indio, United States",
    "Devon, United Kingdom",
    "Agde, France",
    "Oaxaca, Mexico",
    "Merida, Mexico",
    "La Rochelle, France",
    "Helsinki, Finland",
    "Prague, Czechia",
    "Zakopane, Poland",
    "Incline Village, United States",
    "Cartagena, Colombia",
    "El Paso, United States",
    "Cincinnati, United States",
    "Durham, United States",
    "Napa, United States",
    "Saint Petersburg, Russia",
    "Avignon, France",
    "San José, Costa Rica",
    "Berkeley, United States",
    "Bradenton, United States",
    "St Petersburg, United States",
    "Baguio, Philippines",
    "Makati, Philippines",
    "Flagstaff, United States",
    "Ipojuca, Brazil",
    "Marco Island, United States",
    "Torrevieja, Spain",
    "La Quinta, United States",
    "Santa Fe, United States",
    "Lisboa, Portugal",
    "Pompano Beach, United States",
    "Hamburg, Germany",
    "Fethiye, Turkey",
    "Reykjavík, Iceland",
    "Seogwipo-si, South Korea",
    "New Smyrna Beach, United States",
    "Jerusalem, Israel",
    "Viña del Mar, Chile",
    "Melbourne, Australia",
    "Fuengirola, Spain",
    "Rochester, United States",
    "Curitiba, Brazil",
    "Bertioga, Brazil",
    "Stateline, United States",
    "Greater Manchester, United Kingdom",
    "Dorset, United Kingdom",
    "Hong Kong, Hong Kong",
    "Cabo San Lucas, Mexico",
    "Princeville, United States",
    "Kent, United Kingdom",
    "Shinjuku City, Japan",
    "Memphis, United States",
    "Fayetteville, United States",
    "Winter Park, United States",
    "Belém, Brazil",
    "Columbia, United States",
    "Frisco, United States",
    "Virginia Beach, United States",
    "Kyoto, Japan",
    "La Serena, Chile",
    "Ashville, United States",
    "Corpus Christi, United States",
    "Yerevan, Armenia",
    "Pula, Croatia",
    "Greenville, United States",
    "Monterrey, Mexico",
    "Zagreb, Croatia",
    "Strasbourg, France",
    "Estes Park, United States",
    "Lagos, Portugal",
    "Estepona, Spain",
    "Verona, Italy",
    "Omaha, United States",
    "Catania, Italy",
    "Capão da Canoa, Brazil",
    "Malacca, Malaysia",
    "Santiago de Querétaro, Mexico",
    "Cambridge, United States",
    "Paraty, Brazil",
    "Carolina Beach, United States",
    "Hot Springs, United States",
    "Guarapari, Brazil",
    "Abidjan, Côte d’Ivoire",
    "Sofia, Bulgaria",
    "Edmonton, Canada",
    "Fort Worth, United States",
    "Las Palmas de Gran Canaria, Spain",
    "West Palm Beach, United States",
    "Oceanside, United States",
    "Cumbria, United Kingdom",
    "Augusta, United States",
    "Big Bear, United States",
    "Keystone, United States",
    "Quận 1, Vietnam",
    "Petaling Jaya, Malaysia",
    "Nantes, France",
    "Lexington, United States",
    "Avon, United States",
    "Tagaytay, Philippines",
    "Athens, United States",
    "Eugene, United States",
    "Lake Havasu City, United States",
    "Oxford, United States",
    "Agadir, Morocco",
    "Funchal, Portugal",
    "Khet Khlong Toei, Thailand",
    "Rodos, Greece",
    "New Delhi, India",
    "Taguig, Philippines",
    "Arraial do Cabo, Brazil",
    "Gramado, Brazil",
    "Mumbai, India",
    "Glendale, United States",
    "Panama City, United States",
    "Baltimore, United States",
    "North Yorkshire, United Kingdom",
    "Caldas Novas, Brazil",
    "Santa Catarina, Brazil",
    "Riga, Latvia",
    "Clermont, United States",
    "Cheju, South Korea",
    "Campos do Jordão, Brazil",
    "Boise, United States",
    "Torremolinos, Spain",
    "Caraguatatuba, Brazil",
    "Benidorm, Spain",
    "Saint-Raphaël, France",
    "Joshua Tree, United States",
    "Newport Beach, United States",
    "Dénia, Spain",
    "Santiago de los Caballeros, Dominican Republic",
    "Tromsø, Norway",
    "Surfers Paradise, Australia",
    "Aix-en-Provence, France",
    "Saratoga Springs, United States",
    "Tangier, Morocco",
    "Montevideo, Uruguay",
    "Puerto Peñasco, Mexico",
    "Sarandë, Albania",
    "Oklahoma City, United States",
    "Santa Cruz de la Sierra, Bolivia",
    "Sumida City, Japan",
    "Pucón, Chile",
    "Springfield, United States",
    "Newport, United States",
    "Belo Horizonte, Brazil",
    "Olímpia, Brazil",
    "Koloa, United States",
    "Whistler, Canada",
    "Key West, United States",
    "Corfu, Greece",
    "Mesa, United States",
    "Durango, United States",
    "Paros, Greece",
    "Bình Thạnh, Vietnam",
    "Almaty, Kazakhstan",
    "Praha 1, Czechia",
    "Porto-Vecchio, France",
    "Le Mans, France",
    "Córdoba, Spain",
    "Leipzig, Germany",
    "Cuenca, Ecuador",
    "Queenstown, New Zealand",
    "Porto Alegre, Brazil",
    "Fort Myers, United States",
    "Norfolk, United Kingdom",
    "Gainesville, United States",
    "Jackson, United States",
    "Traverse City, United States",
    "George Town, Malaysia",
    "Chamonix, France",
    "Cádiz, Spain",
    "Watthana, Thailand",
    "Kansas City, United States",
    "Sacramento, United States",
    "Fatih, Turkey",
    "Merseyside, United Kingdom",
    "Davao City, Philippines",
    "San Miguel de Allende, Mexico",
    "Lille, France",
    "Gurugram, India",
    "Muang Pattaya, Thailand",
    "Nerja, Spain",
    "Milwaukee, United States",
    "Calp, Spain",
    "Kota Kinabalu, Malaysia",
    "Buffalo, United States",
    "Cocoa Beach, United States",
    "Tallinn, Estonia",
    "Mandaluyong, Philippines",
    "Santa Barbara, United States",
    "Santa Clara, United States",
    "Brighton and Hove, United Kingdom",
    "Copacabana, Brazil",
    "Rockport, United States",
    "Tacoma, United States",
    "Bangkok, Thailand",
    "Tallahassee, United States",
    "Noord, Aruba",
    "Oak Island, United States",
    "Blue Ridge, United States",
    "Ilhabela, Brazil",
    "Englewood, United States",
    "Amman, Jordan",
    "Lincoln, United States",
    "Palermo, Argentina",
    "Khet Huai Khwang, Thailand",
    "Panamá, Panama",
    "Sunny Isles Beach, United States",
    "Siesta Key, United States",
    "Sarajevo, Bosnia & Herzegovina",
    "Fortaleza, Brazil",
    "Itapema, Brazil",
    "Boulder, United States",
    "Hyères, France",
    "Kill Devil Hills, United States",
    "Maceió, Brazil",
    "Trondheim, Norway",
    "Lagos, Nigeria",
    "Rhodes, Greece",
    "Rovinj, Croatia",
    "Christchurch, New Zealand",
    "Franklin, United States",
    "Portimão, Portugal",
    "Moscow, Russia",
    "Genoa, Italy",
    "Santo Domingo Este, Dominican Republic",
    "Lake Arrowhead, United States",
    "Syracuse, Italy",
    "Ruidoso, United States",
    "Garopaba, Brazil",
    "Sandton, South Africa",
    "Alexandria, United States",
    "St. George, United States",
    "Tempe, United States",
    "Ottawa, Canada",
    "Toulon, France",
    "Saint-Malo, France",
    "Córdoba, Argentina",
    "Highland Council, United Kingdom",
    "Palo Alto, United States",
    "Fréjus, France",
    "Las Terrenas, Dominican Republic",
    "South Bend, United States",
    "Budva, Montenegro",
    "Vilnius, Lithuania",
    "Alanya, Turkey",
    "Knoxville, United States",
    "Wildwood, United States",
    "Cologne, Germany",
    "Carolina, Puerto Rico",
    "Les Sables-d'Olonne, France",
    "Quarteira, Portugal",
    "Leavenworth, United States",
    "New Braunfels, United States",
    "Hallandale Beach, United States",
    "Bergenhus, Norway",
    "La Paz, Mexico",
    "Coquimbo, Chile",
    "Muratpaşa, Turkey",
    "Detroit, United States",
    "Tybee Island, United States",
    "Biarritz, France",
    "Mountain View, United States",
    "Tulsa, United States",
    "Zapopan, Mexico",
    "Bodrum, Turkey",
    "Frederiksberg, Denmark",
    "Recife, Brazil",
    "Lake Placid, United States",
    "Kings Beach, United States",
    "Hoàn Kiếm, Vietnam",
    "Valparaíso, Chile",
    "Jaipur, India",
    "Marathon, United States",
    "East Hampton, United States",
    "Barranquilla, Colombia",
    "Nha Trang, Vietnam",
    "Sète, France",
    "Brașov, Romania",
    "Yucca Valley, United States",
    "Zürich, Switzerland",
    "Goiânia, Brazil",
    "Ipoh, Malaysia",
    "Jeddah, Saudi Arabia",
    "Durrës, Albania",
    "Sosúa, Dominican Republic",
    "Lapu-Lapu City, Philippines",
    "Santa Cruz de Tenerife, Spain",
    "Santos, Brazil",
    "Taito City, Japan",
    "Ithaca, United States",
    "Sunriver, United States",
    "Gloucestershire, United Kingdom",
    "Tijuana, Mexico",
    "Dublin, Ireland",
    "Salem, United States",
    "Aspen, United States",
    "Imbituba, Brazil",
    "Moab, United States",
    "Costa Adeje, Spain",
    "Kingston, Jamaica",
    "Sơn Trà, Vietnam",
    "Zakinthos, Greece",
    "CARTAGENA, Colombia",
    "Odesa, Ukraine",
    "Montgomery, United States",
    "Puebla, Mexico",
    "Providencia, Chile",
    "St. Simons Island, United States",
    "Key Largo, United States",
    "Mykonos, Greece",
    "Angra dos Reis, Brazil",
    "Lubbock, United States",
    "Guayaquil, Ecuador",
    "Rosarito, Mexico",
    "Foz do Iguaçu, Brazil",
    "Daly City, United States",
    "Governador Celso Ramos, Brazil",
    "Salou, Spain",
    "Birmingham, United States",
    "Makarska, Croatia",
    "Olympic Valley, United States",
    "Kampala, Uganda",
    "Reno, United States",
    "Guatemala City, Guatemala",
    "Poznań, Poland",
    "Carnelian Bay, United States",
    "Willemstad, Curaçao",
    "Cagliari, Italy",
    "Oxfordshire, United Kingdom",
    "Fernandina Beach, United States",
    "Parañaque, Philippines",
    "Madison, United States",
    "Mississauga, Canada",
    "Chattanooga, United States",
    "Şişli, Turkey",
    "Wailuku, United States",
    "Rouen, France",
    "Arcachon, France",
    "Canmore, Canada",
    "Whitefish, United States",
    "Mapo-gu, South Korea",
    "Anaheim, United States",
    "Treasure Island, United States",
    "Novalja, Croatia",
    "Morzine, France",
    "Essaouira, Morocco",
    "Heraklion, Greece",
    "Lucca, Italy",
    "Carlsbad, United States",
    "Albany, United States",
    "Varna, Bulgaria",
    "Aarhus, Denmark",
    "Palhoça, Brazil",
    "Vlorë, Albania",
    "Cardiff, United Kingdom",
    "Ndakhar, Senegal",
    "Lakewood, United States",
    "Indian Rocks Beach, United States",
    "Antigua Guatemala, Guatemala",
    "Canyon Lake, United States",
    "La Spezia, Italy",
    "Sorrento, Italy",
    "Belfast, United Kingdom",
    "Holmes Beach, United States",
    "Alghero, Italy",
    "Grünerløkka, Norway",
    "Conil de la Frontera, Spain",
    "Grenoble, France",
    "Ensenada, Mexico",
    "Pagosa Springs, United States",
    "Rovaniemi, Finland",
    "Arona, Spain",
    "Ajaccio, France",
    "Pretoria, South Africa",
    "Tahoe Vista, United States",
    "Pensacola Beach, United States",
    "West Yorkshire, United Kingdom",
    "Bratislava, Slovakia",
    "Hyderabad, India",
    "Navarre, United States",
    "Düsseldorf, Germany",
    "Islamabad, Pakistan",
    "Matinhos, Brazil",
    "Jung-gu, South Korea",
    "Reims, France",
    "Warszawa, Poland",
    "Manila, Philippines",
    "Itanhaém, Brazil",
    "Bryson City, United States",
    "Hvar, Croatia",
    "Pirenópolis, Brazil",
    "Surfside Beach, United States",
    "Telluride, United States",
    "Bilbao, Spain",
    "Hudson, United States",
    "Big Sky, United States",
    "Cartagena de Indias, Colombia",
    "Tarifa, Spain",
    "Rehoboth Beach, United States",
    "Charlottesville, United States",
    "Lacanau, France",
    "Fort Myers Beach, United States",
    "Palm Coast, United States",
    "Hampton, United States",
    "Crested Butte, United States",
    "Woodstock, United States",
    "Ljubljana, Slovenia",
    "Le Grau-du-Roi, France",
    "Rabat, Morocco",
    "Zihuatanejo, Mexico",
    "Nassau, Bahamas",
    "Santa Monica, United States",
    "Corralejo, Spain",
    "Roses, Spain",
    "Osage Beach, United States",
    "Camaçari, Brazil",
    "Decatur, United States",
    "La Grande-Motte, France",
    "Hampshire, United Kingdom",
    "Las Condes, Chile",
    "Aurora, United States",
    "Dijon, France",
    "Silverthorne, United States",
    "Guanajuato, Mexico",
    "West Sussex, United Kingdom",
    "Auburn, United States",
    "Petrópolis, Brazil",
    "Toshima City, Japan",
    "Hội An, Vietnam",
    "Bloomington, United States",
    "Greensboro, United States",
    "Antwerp, Belgium",
    "Nîmes, France",
    "Ngũ Hành Sơn, Vietnam",
    "Rennes, France",
    "Pa Tong, Thailand",
    "Santander, Spain",
    "Port Charlotte, United States",
    "San Salvador, El Salvador",
    "Marrakech, Morocco",
    "Puerto Escondido, Mexico",
    "East Sussex, United Kingdom",
    "Québec, Canada",
    "Montréal, Canada",
    "Paso Robles, United States",
    "Donostia-San Sebastian, Spain",
    "Mijas, Spain",
    "Norfolk, United States",
    "Iskandar Puteri, Malaysia",
    "Bellevue, United States",
    "Cluj-Napoca, Romania",
    "Ellijay, United States",
    "Arles, France",
    "Venice, United States",
    "Dillon, United States",
    "Shah Alam, Malaysia",
    "Logan, United States",
    "Chișinău, Moldova",
    "Ao Nang, Thailand",
    "Waco, United States",
    "Chiclana de la Frontera, Spain",
    "Bonita Springs, United States",
    "Mombasa, Kenya",
    "Sayulita, Mexico",
    "Corolla, United States",
    "Bozeman, United States",
    "Port St. Joe, United States",
    "Tamarindo, Costa Rica",
    "Valdivia, Chile",
    "Lviv, Ukraine",
    "Island Park, United States",
    "La Ciotat, France",
    "Beech Mountain, United States",
    "North Topsail Beach, United States",
    "Aguascalientes, Mexico",
    "Isle of Palms, United States",
    "Gamle Oslo, Norway",
    "Port Angeles, United States",
    "Granby, United States",
    "Lancaster, United States",
    "Canet-en-Roussillon, France",
    "Stowe, United States",
    "Dover, United States",
    "Lahore, Pakistan",
    "Como, Italy",
    "Menton, France",
    "Killington, United States",
    "Sapanca, Turkey",
    "Asunción, Paraguay",
    "Irvine, United States",
    "València, Spain",
    "Lafayette, United States",
    "Eilat, Israel",
    "Bourg-Saint-Maurice, France",
    "Suffolk, United Kingdom",
    "Çeşme, Turkey",
    "Dresden, Germany",
    "Puerto Vallarta, Mexico",
    "York, United Kingdom",
    "Lège-Cap-Ferret, France",
    "West Hollywood, United States",
    "Praha 2, Czechia",
    "La Baule-Escoublac, France",
    "Algarrobo, Chile",
    "Hayward, United States",
    "Vila Velha, Brazil",
    "Johannesburg, South Africa",
    "Arvada, United States",
    "Somerset, United Kingdom",
    "Largo, United States",
    "Henderson, United States",
    "Ocala, United States",
    "Phnom Penh, Cambodia",
    "Delray Beach, United States",
    "Victoria, Canada",
    "Coeur d'Alene, United States",
    "Crikvenica, Croatia",
    "Leon, Mexico",
    "Rapid City, United States",
    "Salinópolis, Brazil",
    "Brest, France",
    "Faro, Portugal",
    "Cuernavaca, Mexico",
    "Spokane, United States",
    "Ann Arbor, United States",
    "Rawai, Thailand",
    "San Bartolomé de Tirajana, Spain",
    "Fira, Greece",
    "Saint-Cyprien, France",
    "Sainte-Maxime, France",
    "Hendersonville, United States",
    "Boulogne-Billancourt, France",
    "Mill Valley, United States",
    "Huntsville, United States",
    "Gwynedd, United Kingdom",
    "Gangneung-si, South Korea",
    "Gijón, Spain",
    "Madeira Beach, United States",
    "Beverly Hills, United States",
    "Lynchburg, United States",
    "Pune, India",
    "Garden City, United States",
    "Incheon, South Korea",
    "Bentonville, United States",
    "Quintana Roo, Mexico",
    "Lincoln City, United States",
    "Syracuse, United States",
    "Lekki, Nigeria",
    "Anglet, France",
    "Georgetown, United States",
    "Concón, Chile",
    "Gaira, Colombia",
    "Lloret de Mar, Spain",
    "Quận 4, Vietnam",
    "Providence, United States",
    "Puerto Varas, Chile",
    "Atlantic Beach, United States",
    "Hanover, Germany",
    "Le Barcarès, France",
    "Nuevo Vallarta, Mexico",
    "Seaside, United States",
    "Baton Rouge, United States",
    "Saint-Denis, France",
    "Cochabamba, Bolivia",
    "Angel Fire, United States",
    "Sokcho-si, South Korea",
    "Villeurbanne, France",
    "Rijeka, Croatia",
    "Port St. Lucie, United States",
    "Sandy, United States",
    "North Charleston, United States",
    "Saint Paul, United States",
    "Skopje, North Macedonia",
    "Pembrokeshire, United Kingdom",
    "Gulfport, United States",
    "San Andrés, Colombia",
    "Argelès-sur-Mer, France",
    "Dayton, United States",
    "Jacksonville Beach, United States",
    "Pereira, Colombia",
    "Stavanger, Norway",
    "Ushuaia, Argentina",
    "Alto Paraíso de Goiás, Brazil",
    "Rethimno, Greece",
    "Xàbia, Spain",
    "Plymouth, United States",
    "Kuching, Malaysia",
    "The Villages, United States",
    "Bolivar Peninsula, United States",
    "Oakhurst, United States",
    "Almería, Spain",
    "Morelia, Mexico",
    "Abu Dhabi, United Arab Emirates",
    "Vũng Tàu, Vietnam",
    "Prescott, United States",
    "Tibau do Sul, Brazil",
    "Dar es Salaam, Tanzania",
    "Union City, United States",
    "Asheville, United States",
    "Mazamitla, Mexico",
    "Nags Head, United States",
    "Tignes, France",
    "La Teste-de-Buch, France",
    "Napoli, Italy",
    "Irving, United States",
    "Baku, Azerbaijan",
    "Arequipa, Peru",
    "Winston-Salem, United States",
    "State College, United States",
    "Kadıköy, Turkey",
    "Gapyeong-gun, South Korea",
    "Illes Balears, Spain",
    "Valle de Bravo, Mexico",
    "Saint-François, Guadeloupe",
    "Indian Shores, United States",
    "Fresno, United States",
    "Cagnes-sur-Mer, France",
    "Surrey, United Kingdom",
    "Penha, Brazil",
    "Isle of Wight, United Kingdom",
    "Six-Fours-les-Plages, France",
    "Kingston, United States",
    "Hertfordshire, United Kingdom",
    "Saint-Gervais-les-Bains, France",
    "Kotor, Montenegro",
    "Middletown, United States",
    "New Cairo 1, Egypt",
    "Atlantic City, United States",
    "Noida, India",
    "Folly Beach, United States",
    "Conway, United States",
    "Hurricane, United States",
    "Montego Bay, Jamaica",
    "Glasgow, United Kingdom",
    "Cape Canaveral, United States",
    "Capbreton, France",
    "La Paz, Bolivia",
    "Missoula, United States",
    "Santa Ana, United States",
    "Kigali, Rwanda",
    "Angeles, Philippines",
    "Winnipeg, Canada",
    "Villa de Leyva, Colombia",
    "Hurghada, Egypt",
    "Ba Đình, Vietnam",
    "Playa Blanca, Spain",
    "Gqeberha, South Africa",
    "Seogwipo, South Korea",
    "Bucerías, Mexico",
    "Idyllwild-Pine Cove, United States",
    "Jaco, Costa Rica",
    "Olbia, Italy",
    "Sliema, Malta",
    "Guwahati, India",
    "Dalat, Vietnam",
    "Redmond, United States",
    "Okrug Gornji, Croatia",
    "Burlington, United States",
    "Arnold, United States",
    "South Haven, United States",
    "Tây Hồ, Vietnam",
    "Tyne and Wear, United Kingdom",
    "Provincetown, United States",
    "Biscarrosse, France",
    "Alajuela, Costa Rica",
    "Marietta, United States",
    "Genting Highlands, Malaysia",
    "Orihuela, Spain",
    "Naousa, Greece",
    "Paphos, Cyprus",
    "Trieste, Italy",
    "Empuriabrava, Spain",
    "Bakersfield, United States",
    "Kolkata, India",
    "Sopot, Poland",
    "Puerto Plata, Dominican Republic",
    "Tôrres, Brazil",
    "Pasadena, United States",
    "Boone, United States",
    "Encinitas, United States",
    "Blumenau, Brazil",
    "Pichilemu, Chile",
    "Plettenberg Bay, South Africa",
    "Vigo, Spain",
    "La Fortuna, Costa Rica",
    "Cle Elum, United States",
    "Snowmass Village, United States",
    "Varanasi, India",
    "Wisconsin Dells, United States",
    "Angers, France",
    "Siena, Italy",
    "Fairbanks, United States",
    "San José del Cabo, Mexico",
    "Natal, Brazil",
    "Narbonne, France",
    "Campinas, Brazil",
    "Sevilla, Spain",
    "Brussels, Belgium",
    "Banner Elk, United States",
    "Bradenton Beach, United States",
    "Waikoloa Village, United States",
    "Sapporo, Japan",
    "Wellington, New Zealand",
    "College Station, United States",
    "دبي, United Arab Emirates",
    "Fraser, United States",
    "Tours, France",
    "Murrells Inlet, United States",
    "Colmar, France",
    "Kościelisko, Poland",
    "San Miguel de Cozumel, Mexico",
    "Les Belleville, France",
    "Surf City, United States",
    "La Romana, Dominican Republic",
    "Gérardmer, France",
    "Carvoeiro, Portugal",
    "Niagara Falls, Canada",
    "Villarrica, Chile",
    "Sunnyvale, United States",
    "Vannes, France",
    "Lake George, United States",
    "Almuñécar, Spain",
    "Haifa, Israel",
    "Bristol, United States",
    "Saint-Paul, Réunion",
    "Beaver Creek, United States",
    "Pollença, Spain",
    "Falmouth, United States",
    "Brampton, Canada",
    "Manzanillo, Mexico",
    "Chandler, United States",
    "Santa Cruz, United States",
    "Gilbert, United States",
    "Pacifica, United States",
    "Larnaca, Cyprus",
    "Plano, United States",
    "Olomouc, Czechia",
    "Hermosillo, Mexico",
    "Hoboken, United States",
    "Florence, United States",
    "Łódź, Poland",
    "Dolphin Coast, South Africa",
    "North Bergen, United States",
    "Mata de São João, Brazil",
    "Windham, United States",
    "Redwood City, United States",
    "Royan, France",
    "Tobyhanna, United States",
    "Perpignan, France",
    "Menlo Park, United States",
    "Maggie Valley, United States",
    "Novi Sad, Serbia",
    "Harare, Zimbabwe",
    "La Seyne-sur-Mer, France",
    "L'Escala, Spain",
    "The Bronx, United States",
    "Acapulco, Mexico",
    "Manta, Ecuador",
    "Khet Ratchathewi, Thailand",
    "Lancashire, United Kingdom",
    "Narragansett, United States",
    "Eureka Springs, United States",
    "Oshkosh, United States",
    "Ormond Beach, United States",
    "Constanța, Romania",
    "Dennis, United States",
    "Fremont, United States",
    "Zephyr Cove, United States",
    "Carcassonne, France",
    "Katowice, Poland",
    "Saugerties, United States",
    "Northumberland, United Kingdom",
    "Salerno, Italy",
    "Iloilo City, Philippines",
    "Saint-Jean-de-Monts, France",
    "McHenry, United States",
    "Warren, United States",
    "Sanary-sur-Mer, France",
    "Homer, United States",
    "Krong Siem Reap, Cambodia",
    "Des Moines, United States",
    "Tamandaré, Brazil",
    "Punta del Diablo, Uruguay",
    "Taupō, New Zealand",
    "Barnstable, United States",
    "Nazaré, Portugal",
    "Gruissan, France",
    "Huez, France",
    "Fort Collins, United States",
    "Taormina, Italy",
    "Blackpool, United Kingdom",
    "Chennai, India",
    "Porto de Galinhas, Brazil",
    "Bellingham, United States",
    "Old Orchard Beach, United States",
    "Beirut, Lebanon",
    "Essex, United Kingdom",
    "Kitty Hawk, United States",
    "Singapore, Singapore",
    "Beaufort, United States",
    "Papudo, Chile",
    "Sonoma, United States",
    "Peoria, United States",
    "Waimea, United States",
    "Kuantan, Malaysia",
    "Guaratuba, Brazil",
    "Nantucket, United States",
    "Aix-les-Bains, France",
    "Phu Quoc, Vietnam",
    "Huntington Beach, United States",
    "Brisas de Zicatela, Mexico",
    "Westminster, United States",
    "Sharjah, United Arab Emirates",
    "Mimizan, France",
    "Pasig, Philippines",
    "Pontal do Paraná, Brazil",
    "Basel, Switzerland",
    "București, Romania",
    "Les Deux Alpes, France",
    "Cabarete, Dominican Republic",
    "Dinard, France",
    "Gdynia, Poland",
    "A Coruña, Spain",
    "Le Havre, France",
    "Mount Vernon, United States",
    "East Stroudsburg, United States",
    "Choeng Thale, Thailand",
    "Montreuil, France",
    "Alameda, United States",
    "Yarmouth, United States",
    "Roquebrune-sur-Argens, France",
    "Graz, Austria",
    "Tavira, Portugal",
    "Praha 3, Czechia",
    "Palma, Spain",
    "Manchester, United States",
    "Geneva, United States",
    "Jerez de la Frontera, Spain",
    "Lincolnshire, United Kingdom",
    "Twentynine Palms, United States",
    "Ribeirao Preto, Brazil",
    "Maspalomas, Spain",
    "Clarksville, United States",
    "Trogir, Croatia",
    "None, Greece",
    "Melbourne, United States",
    "Cefalù, Italy",
    "Orléans, France",
    "North Las Vegas, United States",
    "Gyeongju-si, South Korea",
    "Peruíbe, Brazil",
    "Bayonne, France",
    "Candolim, India",
    "Anna Maria, United States",
    "Pisa, Italy",
    "Fes, Morocco",
    "Wailea-Makena, United States",
    "Annapolis, United States",
    "Urubici, Brazil",
    "Tramandaí, Brazil",
    "Vila Nova de Gaia, Portugal",
    "Podstrana, Croatia",
    "Wānaka, New Zealand",
    "Kapaʻa, United States",
    "Bansko, Bulgaria",
    "Xangri-lá, Brazil",
    "Tambon Bo Put, Thailand",
    "Geneva, Switzerland",
    "New Haven, United States",
    "Salta, Argentina",
    "Stuttgart, Germany",
    "Elizabeth, United States",
    "Quincy, United States",
    "Chihuahua, Mexico",
    "Seignosse, France",
    "Puerto Viejo de Talamanca, Costa Rica",
    "Puerto de la Cruz, Spain",
    "Rio Grande do Sul, Brazil",
    "Hamilton, Canada",
    "Cauterets, France",
    "Palanga, Lithuania",
    "Sitges, Spain",
    "Southbank, Australia",
    "San Juan, Philippines",
    "Lead, United States",
    "Recoleta, Argentina",
    "Sanremo, Italy",
    "Quepos, Costa Rica",
    "Lakeland, United States",
    "Bartlett, United States",
    "San Martín de los Andes, Argentina",
    "Tampere, Finland",
    "Fort Pierce, United States",
    "Oslo, Norway",
    "Desert Hot Springs, United States",
    "Wimberley, United States",
    "Surrey, Canada",
    "Bergamo, Italy",
    "Mont-Tremblant, Canada",
    "Medulin, Croatia",
    "Cascais, Portugal",
    "Gangneung, South Korea",
    "Balneário Piçarras, Brazil",
    "Armenia, Colombia",
    "Temecula, United States",
    "Buena Vista, United States",
    "Jefferson, United States",
    "Derbyshire, United Kingdom",
    "Grand Junction, United States",
    "Khet Watthana, Thailand",
    "Girona, Spain",
    "Essen, Germany",
    "Sainte-Anne, Guadeloupe",
    "West New York, United States",
    "Monticello, United States",
    "Southampton, United States",
    "Le Lavandou, France",
    "Caen, France",
    "Deerfield Beach, United States",
    "Cambridgeshire, United Kingdom",
    "Tías, Spain",
    "Ponta Delgada, Portugal",
    "Saint-Étienne, France",
    "Montauk, United States",
    "Salinas, Ecuador",
    "Ludlow, United States",
    "Bath and North East Somerset, United Kingdom",
    "South San Francisco, United States",
    "Mamaia-Sat, Romania",
    "Torbay, United Kingdom",
    "Bar Harbor, United States",
    "Canton, United States",
    "Vero Beach, United States",
    "Caracas, Venezuela",
    "Riverside, United States",
    "Megève, France",
    "Dehradun, India",
    "Saint-Ouen-sur-Seine, France",
    "Mobile, United States",
    "Livingston, United States",
    "Barranco, Peru",
    "Second New Cairo, Egypt",
    "Grand Baie, Mauritius",
    "Rockaway Beach, United States",
    "Kołobrzeg, Poland",
    "Hua Hin, Thailand",
    "Uvita, Costa Rica",
    "Wrightsville Beach, United States",
    "Columbia Falls, United States",
    "Fukuoka, Japan",
    "Grand Lake, United States",
    "Poreč, Croatia",
    "Kelowna, Canada",
    "Tepoztlán, Mexico",
    "Bandol, France",
    "Byron Bay, Australia",
    "Ellicottville, United States",
    "Cagayan de Oro, Philippines",
    "Berkshire, United Kingdom",
    "Green Bay, United States",
    "Little Rock, United States",
    "Pinamar, Argentina",
    "Groveland, United States",
    "Kalispell, United States",
    "Alcúdia, Spain",
    "L'Hospitalet de Llobregat, Spain",
    "Renton, United States",
    "El Puerto de Santa María, Spain",
    "Astana, Kazakhstan",
    "Redding, United States",
    "Clermont-Ferrand, France",
    "Spring, United States",
    "Malibu, United States",
    "Three Rivers, United States",
    "Canasvieiras, Brazil",
    "Dauphin Island, United States",
    "General Luna, Philippines",
    "Bryan, United States",
    "Concord, United States",
    "Murcia, Spain",
    "Aljezur, Portugal",
    "Langkawi, Malaysia",
    "Trapani, Italy",
    "Nancy, France",
    "Castellammare del Golfo, Italy",
    "Grand Prairie, United States",
    "Cape May, United States",
    "Cambrils, Spain",
    "Seaside Heights, United States",
    "Bremen, Germany",
    "Galway, Ireland",
    "Rogers, United States",
    "Cavalaire-sur-Mer, France",
    "Iquique, Chile",
    "Calvi, France",
    "Aracaju, Brazil",
    "Amarillo, United States",
    "Covington, United States",
    "Fairplay, United States",
    "Prince Edward, Canada",
    "York, United States",
    "Itacaré, Brazil",
    "Kapolei, United States",
    "Ocean Isle Beach, United States",
    "Kallithea, Greece",
    "None, United States",
    "Itapoá, Brazil",
    "Beşiktaş, Turkey",
    "Luján de Cuyo, Argentina",
    "Mount Pleasant, United States",
    "Tahoma, United States",
    "Hamilton, United States",
    "Lake Lure, United States",
    "Jensen Beach, United States",
    "Ashford, United States",
    "Vodice, Croatia",
    "Williams, United States",
    "Jarabacoa, Dominican Republic",
    "Knysna, South Africa",
    "Silver Spring, United States",
    "Kristiansand, Norway",
    "Maraú, Brazil",
    "Wichita, United States",
    "Tannersville, United States",
    "Quartu Sant'Elena, Italy",
    "Le Gosier, Guadeloupe",
    "Davis, United States",
    "Brian Head, United States",
    "Taean-gun, South Korea",
    "Richmond Hill, Canada",
    "St. Pete Beach, United States",
    "Shibuya, Japan",
    "San Luis Obispo, United States",
    "Freeport, United States",
    "Clayton, United States",
    "Perugia, Italy",
    "Punta Gorda, United States",
    "Geoje-si, South Korea",
    "Oranjestad, Aruba",
    "Sarlat-la-Canéda, France",
    "Black Mountain, United States",
    "Padua, Italy",
    "Galena, United States",
    "La Plagne-Tarentaise, France",
    "Lonavala, India",
    "Yuma, United States",
    "Jamestown, United States",
    "Rimini, Italy",
    "Le Touquet, France",
    "Saint-Tropez, France",
    "Zaragoza, Spain",
    "Ashland, United States",
    "Quận 2, Vietnam",
    "Wells, United States",
    "Ocho Rios, Jamaica",
    "Saint-Lary-Soulan, France",
    "Setúbal, Portugal",
    "Manali, India",
    "Canela, Brazil",
    "Rosario, Argentina",
    "Lansing, United States",
    "Snowshoe, United States",
    "Clinton, United States",
    "Duluth, United States",
    "Ronda, Spain",
    "South Yorkshire, United Kingdom",
    "Chatham, United States",
    "Yeosu-si, South Korea",
    "Bethany Beach, United States",
    "Tonsupa, Ecuador",
    "Holden Beach, United States",
    "Kiawah Island, United States",
    "Mazatlán, Mexico",
    "Culver City, United States",
    "Cabourg, France",
    "Saint-Hilaire-de-Riez, France",
    "Alhambra, United States",
    "Les Allues, France",
    "Cassis, France",
    "Lake Ozark, United States",
    "Puerto Morelos, Mexico",
    "Marion, United States",
    "Świnoujście, Poland",
    "Trouville-sur-Mer, France",
    "Southampton, United Kingdom",
    "McCall, United States",
    "Waynesville, United States",
    "Heroica Veracruz, Mexico",
    "Burgas, Bulgaria",
    "Torrox, Spain",
    "Ostend, Belgium",
    "São Vicente, Brazil",
    "Ilhéus, Brazil",
    "Bacolod, Philippines",
    "San Cristobal de las Casas, Mexico",
    "Chelan, United States",
    "Amiens, France",
    "Kalamata, Greece",
    "Cyberjaya, Malaysia",
    "T'bilisi, Georgia",
    "Jeonju, South Korea",
    "Chiang Mai, Thailand",
    "Malay, Philippines",
    "Bagnères-de-Bigorre, France",
    "Prado, Brazil",
    "Envigado, Colombia",
    "Milford, United States",
    "Niagara Falls, United States",
    "Mérida, Mexico",
    "Kathmandu, Nepal",
    "Noosa Heads, Australia",
    "Martil, Morocco",
    "Braga, Portugal",
    "Puerto Iguazú, Argentina",
    "Mongaguá, Brazil",
    "Kochi, India",
    "Nuremberg, Germany",
    "Oia, Greece",
    "Saquarema, Brazil",
    "Johnson City, United States",
    "Brownsville, United States",
    "Spring Hill, United States",
    "Gulf Breeze, United States",
    "Mulhouse, France",
    "Trinidad, Cuba",
    "Smyrna, United States",
    "Sequim, United States",
    "Morganton, United States",
    "Vancouver, United States",
    "Santa Rosa, United States",
    "Lake Harmony, United States",
    "Rotterdam, Netherlands",
    "Littleton, United States",
    "Rotorua, New Zealand",
    "Haines City, United States",
    "Deauville, France",
    "San Isidro, Peru",
    "The Hague, Netherlands",
    "Les Trois-Îlets, Martinique",
    "Peniscola, Spain",
    "Medford, United States",
    "Bol, Croatia",
    "Lihue, United States",
    "San Luis Potosi, Mexico",
    "Odense, Denmark",
    "Juan Dolio, Dominican Republic",
    "Concepción, Chile",
    "Suyeong-gu, South Korea",
    "Billings, United States",
    "Sugar Mountain, United States",
    "Lebanon, United States",
    "San Mateo, United States",
    "Šibenik, Croatia",
    "Midrand, South Africa",
    "Leucate, France",
    "Marina del Rey, United States",
    "Somerville, United States",
    "Puducherry, India",
    "Isla Mujeres, Mexico",
    "Coachella, United States",
    "Victor, United States",
    "Yonkers, United States",
    "Stillwater, United States",
    "Vallauris, France",
    "Halifax, Canada",
    "Portsmouth, United States",
    "Clichy, France",
    "Beograd, Serbia",
    "Liège, Belgium",
    "Tashkent, Uzbekistan",
    "Pinehurst, United States",
    "Packwood, United States",
    "Blowing Rock, United States",
    "Carmel-by-the-Sea, United States",
    "Tegucigalpa, Honduras",
    "Font-Romeu-Odeillo-Via, France",
    "Pontevedra, Spain",
    "Fife, United Kingdom",
    "Bagnères-de-Luchon, France",
    "Emerald Isle, United States",
    "Sanibel, United States",
    "Cheyenne, United States",
    "Krk, Croatia",
    "Gujan-Mestras, France",
    "Manizales, Colombia",
    "Stellenbosch, South Africa",
    "Maragogi, Brazil",
    "Biloxi, United States",
    "Rosemary Beach, United States",
    "Midland, United States",
    "Sochi, Russia",
    "Brigantine, United States",
    "Barra Velha, Brazil",
    "Luz, Portugal",
    "Nottingham, United Kingdom",
    "Vichy, France",
    "St. Julian's, Malta",
    "Plovdiv, Bulgaria",
    "Platja d'Aro i S'Agaró, Spain",
    "Bella Vista, United States",
    "Fort Wayne, United States",
    "Khet Sathon, Thailand",
    "San Vito Lo Capo, Italy",
    "Beausoleil, France",
    "McKinney, United States",
    "Frankfurt, Germany",
    "Lake Worth, United States",
    "Albrightsville, United States",
    "Tarragona, Spain",
    "Salida, United States",
    "Morgantown, United States",
    "Karachi, Pakistan",
    "Vejer de la Frontera, Spain",
    "Palavas-les-Flots, France",
    "Fairfield, United States",
    "Altea, Spain",
    "Randburg, South Africa",
    "St. Paul's Bay, Malta",
    "Kaliningrad, Russia",
    "Flic en Flac, Mauritius",
    "Puerto Montt, Chile",
    "Manaus, Brazil",
    "Koksijde, Belgium",
    "Ixelles, Belgium",
    "San Fernando, Philippines",
    "Mostar, Bosnia & Herzegovina",
    "Nova Friburgo, Brazil",
    "Aquiraz, Brazil",
    "Sanxenxo, Spain",
    "McAllen, United States",
    "Ghent, Belgium",
    "Fažana, Croatia",
    "Olympia, United States",
    "Ota City, Japan",
    "Kuala Terengganu, Malaysia",
    "Sibiu, Romania",
    "uMhlanga, South Africa",
    "Erie, United States",
    "Versailles, France",
    "Tunis, Tunisia",
    "Port Dickson, Malaysia",
    "Oviedo, Spain",
    "Ericeira, Portugal",
    "Carnac, France",
    "Bayfield, United States",
    "Cabedelo, Brazil",
    "Calangute, India",
    "Monroe, United States",
    "Marmaris, Turkey",
    "Tambon Su Thep, Thailand",
    "Ventura, United States",
    "Townsend, United States",
    "Zermatt, Switzerland",
    "Troy, United States",
    "Utrecht, Netherlands",
    "Quận 7, Vietnam",
    "Södermalm, Sweden",
    "Ibagué, Colombia",
    "Maldonado, Uruguay",
    "North Vancouver, Canada",
    "São Thomé das Letras, Brazil",
    "Walnut Creek, United States",
    "Noto, Italy",
    "Benahavís, Spain",
    "Datça, Turkey",
    "Golden, United States",
    "Lefkada, Greece",
    "Las Cruces, United States",
    "Everett, United States",
    "Udaipur, India",
    "Homewood, United States",
    "Kure Beach, United States",
    "Quiberon, France",
    "Honfleur, France",
    "São Lourenço, Brazil",
    "Ouro Preto, Brazil",
    "Bydel Sagene, Norway",
    "Bethel, United States",
    "Hartford, United States",
    "Timișoara, Romania",
    "Saint-Cyr-sur-Mer, France",
    "Burbank, United States",
    "Zandvoort, Netherlands",
    "Wilton Manors, United States",
    "Le Diamant, Martinique",
    "Doral, United States",
    "Viareggio, Italy",
    "Vinales, Cuba",
    "El Campello, Spain",
    "Tanger, Morocco",
    "Lausanne, Switzerland",
    "Haarlem, Netherlands",
    "La Mesa, United States",
    "Westport, United States",
    "Aubervilliers, France",
    "San Teodoro, Italy",
    "Luxembourg, Luxembourg",
    "Rye, Australia",
    "Michigan City, United States",
    "St. John's, Canada",
    "Åre, Sweden",
    "Desenzano del Garda, Italy",
    "Les Angles, France",
    "Kirkland, United States",
    "Mountain Village, United States",
    "Bormes-les-Mimosas, France",
    "Praha 5, Czechia",
    "Ñuñoa, Chile",
    "Grand Rapids, United States",
    "Cairu, Brazil",
    "Paraná, Brazil",
    "Stuart, United States",
    "Courchevel, France",
    "Knokke-Heist, Belgium",
    "Navajo County, United States",
    "Hampton Bays, United States",
    "San Rafael, United States",
    "El Calafate, Argentina",
    "Causeway Coast and Glens, United Kingdom",
    "Vista, United States",
    "Kanab, United States",
    "Puchuncaví, Chile",
    "Dripping Springs, United States",
    "Béziers, France",
    "Abuja, Nigeria",
    "Kaunas, Lithuania",
    "San Pedro, Belize",
    "Helen, United States",
    "Collioure, France",
    "Hermanus, South Africa",
    "Guadalupe, Mexico",
    "Villard-de-Lans, France",
    "Douala, Cameroon",
    "Courbevoie, France",
    "Sag Harbor, United States",
    "Seward, United States",
    "Khet Phra Khanong, Thailand",
    "Princeton, United States",
    "Madinah, Saudi Arabia",
    "East Palo Alto, United States",
    "Winchester, United States",
    "Gyeongju, South Korea",
    "Hossegor, France",
    "Daytona Beach Shores, United States",
    "Lewes, United States",
    "Aiken, United States",
    "Hendaye, France",
    "Podgorica, Montenegro",
    "Pawleys Island, United States",
    "São Francisco do Sul, Brazil",
    "Sioux Falls, United States",
    "Nevada City, United States",
    "Chincoteague, United States",
    "Tambon Chang Khlan, Thailand",
    "Sandpoint, United States",
    "Pau, France",
    "Lorient, France",
    "Bacalar, Mexico",
    "Pāhoa, United States",
    "Rincón, Puerto Rico",
    "Saint-Nazaire, France",
    "Santa Pola, Spain",
    "Richmond, Canada",
    "Lido di Jesolo, Italy",
    "Loveland, United States",
    "Khet Phra Nakhon, Thailand",
    "Turku, Finland",
    "Ulcinj, Montenegro",
    "Brevard, United States",
    "Murfreesboro, United States",
    "Valladolid, Mexico",
    "Adeje, Spain",
]

In [0]:
print(f"Starting collection for {len(TIER2_CITIES)} cities...")

for city in TIER2_CITIES:
    try:
        result = collect_city_data(
            city_name=city,
            output_dir="poi_data",
            collect_pois=True,
            collect_walk_scores=False,
            mode="center"
        )
        

        print(f"\nSuccessfully collected data for {city}")
    except Exception as e:
        print(f"\nError collecting data for {city}: {e}")
        continue

Starting collection for 1400 cities...
DATA COLLECTION: Clearwater, United States
Budget: 60 squares | Radius: 2.19km

[1/3] GRID GENERATION (Dynamic Radius)
----------------------------------------
Generating single center square for Clearwater, United States...
Saved grid to: poi_data/clearwater_united_states_grid.csv

[2/3] POI DATA COLLECTION (Free)
----------------------------------------
Fetching POI data for Clearwater, United States...


Fetching POI categories:  40%|████      | 2/5 [00:00<00:00,  3.94it/s]

  Found 5 restaurants


Fetching POI categories:  60%|██████    | 3/5 [00:00<00:00,  4.64it/s]

Fetching POI categories:  80%|████████  | 4/5 [01:02<00:24, 24.43s/it]

...

  Found 16 bus_stops


Fetching POI categories: 100%|██████████| 5/5 [01:13<00:00, 14.73s/it]


  Found 8 supermarkets
Counting POIs per grid square...


Processing grid: 100%|██████████| 1/1 [00:00<00:00, 343.82it/s]

Saved POI data to: poi_data/adeje_spain_with_pois.csv

COLLECTION COMPLETE
Output file: poi_data/adeje_spain_complete.csv
Total grid squares: 1

Successfully collected data for Adeje, Spain


In [0]:
# Cell to combine all POI data from poi_data folder into a single file

import pandas as pd
import os
from pathlib import Path

# Path to the folder with collected data
poi_data_dir = Path("poi_data")

# Find all complete CSV files (or with_pois if complete doesn't exist)
all_files = list(poi_data_dir.glob("*_complete.csv"))

# If no complete files, try with_pois files
if not all_files:
    all_files = list(poi_data_dir.glob("*_with_pois.csv"))
    print("No _complete.csv files found, using _with_pois.csv files")

print(f"Found {len(all_files)} city data files to combine")

# Read and combine all files
all_dfs = []
for file_path in all_files:
    try:
        df = pd.read_csv(file_path)
        all_dfs.append(df)
        print(f"✓ Loaded {file_path.name}: {len(df)} rows")
    except Exception as e:
        print(f"✗ Error loading {file_path.name}: {e}")

# Combine all dataframes
if all_dfs:
    combined_df = pd.concat(all_dfs, ignore_index=True)
    
    # Remove duplicates based on unique_grid_id if it exists
    if 'unique_grid_id' in combined_df.columns:
        before_dedupe = len(combined_df)
        combined_df = combined_df.drop_duplicates(subset=['unique_grid_id'], keep='last')
        after_dedupe = len(combined_df)
        if before_dedupe > after_dedupe:
            print(f"\nRemoved {before_dedupe - after_dedupe} duplicate rows")
    
    # Reorder columns to put identifiers first
    id_cols = ['unique_grid_id', 'city_name', 'country_name']
    existing_id_cols = [c for c in id_cols if c in combined_df.columns]
    other_cols = [c for c in combined_df.columns if c not in id_cols]
    combined_df = combined_df[existing_id_cols + other_cols]
    
    # Create output directory and save
    os.makedirs("poi_data", exist_ok=True)
    output_path = "poi_data/GLOBAL_MASTER_DATASET.csv"
    combined_df.to_csv(output_path, index=False)
    
    print("\n" + "=" * 60)
    print("COMBINATION COMPLETE")
    print("=" * 60)
    print(f"Total cities: {combined_df['city_name'].nunique() if 'city_name' in combined_df.columns else 'N/A'}")
    print(f"Total grid squares: {len(combined_df)}")
    print(f"Output saved to: {output_path}")
    print(f"\nColumns: {list(combined_df.columns)}")
else:
    print("\n⚠️ No data files were successfully loaded!")

Found 1523 city data files to combine
✓ Loaded lima_peru_complete.csv: 1 rows
✓ Loaded kingston_united_states_complete.csv: 1 rows
✓ Loaded angeles_philippines_complete.csv: 1 rows
✓ Loaded trieste_italy_complete.csv: 1 rows
✓ Loaded incline_village_united_states_complete.csv: 1 rows
✓ Loaded san_josé_costa_rica_complete.csv: 1 rows
✓ Loaded seville_spain_complete.csv: 62 rows
✓ Loaded steamboat_springs_united_states_complete.csv: 62 rows
✓ Loaded thessaloniki_greece_complete.csv: 1 rows
✓ Loaded bucharest_romania_complete.csv: 1 rows
✓ Loaded agde_france_complete.csv: 1 rows
✓ Loaded helsinki_finland_complete.csv: 1 rows
✓ Loaded prague_czechia_complete.csv: 1 rows
✓ Loaded penha_brazil_complete.csv: 1 rows
✓ Loaded arnold_united_states_complete.csv: 1 rows
✓ Loaded burlington_united_states_complete.csv: 1 rows
✓ Loaded encinitas_united_states_complete.csv: 1 rows
✓ Loaded bakersfield_united_states_complete.csv: 1 rows
✓ Loaded boone_united_states_complete.csv: 1 rows
✓ Loaded los_ang

In [0]:
combined_df = pd.read_csv("poi_data/GLOBAL_MASTER_DATASET.csv")
spark_df = spark.createDataFrame(combined_df)
print(spark_df.columns)

['unique_grid_id', 'city_name', 'country_name', 'grid_id', 'center_lat', 'center_lon', 'poi_restaurants', 'poi_cafes', 'poi_transit_stops', 'poi_bus_stops', 'poi_supermarkets', 'poi_total', 'geometry_wkt']


In [0]:
%pip install reverse_geocoder pycountry

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 38.9 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 74.1 MB/s eta 0:00:00
  Created wheel for reverse_geocoder: filename=reverse_geocoder-1.5.1-py3-none-any.whl size=2268069 sha256=62d2dc1450474c20a1897ba95ab69c965a87d4736c93bd48ce9a8a2d40989a37
  Stored in directory: /home/spark-803a03d0-077a-4b1f-8409-5b/.cache/pip/wheels/11/e1/67/6e47f0ad41ea1843d37e1fbe79c6074744a1f4aace641cf800
Successfully built reverse_geocoder
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:

import reverse_geocoder as rg
import pycountry
from pyspark.sql.functions import pandas_udf, col
from pyspark.sql.types import StructType, StructField, StringType
import pandas as pd

# Schema for all 4 columns
location_schema = StructType([
    StructField("city", StringType()),
    StructField("state", StringType()),
    StructField("country", StringType()),
    StructField("country_code", StringType())
])

def get_country_name(cc):
    """Convert ISO country code to full name"""
    try:
        return pycountry.countries.get(alpha_2=cc).name
    except:
        return cc

@pandas_udf(location_schema)
def get_location_info(lat: pd.Series, lon: pd.Series) -> pd.DataFrame:
    n = len(lat)
    results = pd.DataFrame({
        'city': [None] * n,
        'state': [None] * n,
        'country': [None] * n,
        'country_code': [None] * n
    })
    
    valid_mask = lat.notna() & lon.notna()
    
    if valid_mask.any():
        valid_coords = [
            (lat.iloc[i], lon.iloc[i]) 
            for i in range(n) if valid_mask.iloc[i]
        ]
        geocoded = rg.search(valid_coords)
        
        idx = 0
        for i in range(n):
            if valid_mask.iloc[i]:
                results.loc[i, 'city'] = geocoded[idx]['name']
                results.loc[i, 'state'] = geocoded[idx]['admin1']
                results.loc[i, 'country_code'] = geocoded[idx]['cc']
                results.loc[i, 'country'] = get_country_name(geocoded[idx]['cc'])
                idx += 1
    
    return results

spark_df = spark_df.withColumn(
    "location_info",
    get_location_info(col("center_lat"), col("center_lon"))
).select(
    "*",
    col("location_info.city").alias("city"),
    col("location_info.state").alias("state"),
    col("location_info.country").alias("country"),
    col("location_info.country_code").alias("country_code")
).drop("location_info")



In [0]:
t = spark_df.toPandas()

In [0]:
os.makedirs("poi_data", exist_ok=True)
output_path = "poi_data/GLOBAL_MASTER_DATASET2.csv"
t.to_csv(output_path, index=False)